In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from utils import mistral, mixtral, llama2, MIXTRAL, MISTRAL, LLAMA2

/Users/romainfouilland/code/envs/iamu2/lib/python3.9/site-packages/urllib3/__init__.py:34: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(


In [3]:
DO_INITIAL_PROMPTS = False
DO_LLAMA = False

EMBEDDING_MODEL = MISTRAL # MIXTRAL is way slower with no benefits

In [4]:
if DO_INITIAL_PROMPTS:
    _ = mistral("Raconte l'histoire de l'IA en quelques phrases. Réponds en français.")

In [5]:
if DO_INITIAL_PROMPTS:
    _ = mixtral("Raconte l'histoire de l'IA en quelques phrases. Réponds en français.")

In [6]:
if DO_INITIAL_PROMPTS:
    _ = llama2("Raconte l'histoire de l'IA en quelques phrases. Réponds en français.")

In [7]:
# LOAD
from utils import FILES, load_data, to_full_data

data = load_data(FILES)
full_data = to_full_data(data)
data

{'md': [Document(page_content="# Mode secours (aussi appelé mode dégradé)\n## Passage en mode secours\nVous détectez que la téléphonie est passée en mode secours parce que le bandeau de communication SI-SAMU ne fonctionne plus. L'ordinateur affiche un message qui en précise l'origine. Dans cet exemple, le Session Server est inaccessible. Si vous en avez la possibilité, prenez une photo de l'écran avant de fermer le portail SI-SAMU. Quand la téléphonie est en mode secours vous devez alors utiliser le téléphone positionné sur le bureau. \n\n## Réaction du SAMU au passage en mode secours\nLorsque la téléphonie passe en mode secours, le référent ou responsable du SAMU appelle le support N1 et déclare la panne téléphonique. Il faudra ensuite suivre les consignes du support N3 et, avant de vous déconnecter, vérifiez que vous avez bien accès à votre annuaire téléphonique. Une version Excel de l'annuaire est présente dans la bibliothèque. Le support N3 de l'Agence du numérique en santé ouvre u

In [8]:
# SPLIT
from utils import split_MD_then_recursive

all_splits = split_MD_then_recursive(data)
all_splits

[Document(page_content='67  12. Fonctionnement en mode dégradé  En cas de défaillance du bandeau de communication ou du service de distribution des appels (présenté au chapitre 6) ou d’isolation du site locale (ex : panne d’accès réseau), la brique de téléphonie (ACD de secours du marché M1) prend le relai de la distribution des appels.   Dans ce cas, l’ensemble des actions liées à la téléphonie (modification du statut de l’agent, action téléphonique de type transfert, conférence, etc.) se font depuis le téléphone de', metadata={'source': 'resources/SI-Samu_Documentation_produit_SF4_J18HF2_20231219 - mode secours seul.pdf', 'page': 0}),
 Document(page_content='conférence, etc.) se font depuis le téléphone de l’agent, et plus depuis le bandeau, celui-ci étant inactif ou inaccessible.', metadata={'source': 'resources/SI-Samu_Documentation_produit_SF4_J18HF2_20231219 - mode secours seul.pdf', 'page': 0}),
 Document(page_content="Figure 4. Vue de l'écran du poste téléphonique avec notammen

In [9]:
# EMBED
# Find the relevant splits to then submit those to the model
# -> Create embeddings and store them in a vector database
# -> Use Ollama directly to instantiate an embedding model (ChromaDB here for a vector database)
from langchain.vectorstores import Chroma
import os
from langchain.embeddings import HuggingFaceEmbeddings
from langchain_community.embeddings import HuggingFaceInferenceAPIEmbeddings
from langchain_openai import OpenAIEmbeddings
from langchain.embeddings import OllamaEmbeddings

# Run locally
local_embeddings = HuggingFaceEmbeddings(
    model_name="dangvantuan/sentence-camembert-large",
      # "thenlper/gte-large", "intfloat/e5-mistral-7b-instruct" (heavy)
    encode_kwargs={"normalize_embeddings": True}
)

# HuggingFaceInference | Ref.: https://python.langchain.com/docs/integrations/text_embedding/huggingfacehub#hugging-face-inference-api
inference_embeddings = HuggingFaceInferenceAPIEmbeddings(
    api_key=os.environ['HUGGINGFACEHUB_API_TOKEN'], 
    # Good French embedding but doesn't work... | Ref.: https://huggingface.co/dangvantuan/sentence-camembert-large
    model_name="thenlper/gte-large" 
    # "thenlper/gte-large", "sentence-transformers/stsb-xlm-r-multilingual", "sentence-transformers/all-MiniLM-l6-v2", "dangvantuan/sentence-camembert-large"
)

ollama_embeddings = OllamaEmbeddings(
    model=EMBEDDING_MODEL,
    # Ref.: https://api.python.langchain.com/en/latest/embeddings/langchain_community.embeddings.ollama.OllamaEmbeddings.html#langchain_community.embeddings.ollama.OllamaEmbeddings.show_progress
    show_progress=True
)

openai_embeddings = OpenAIEmbeddings()

embeddings = ollama_embeddings
vectorstore = Chroma.from_documents(documents=all_splits, embedding=embeddings)

pytorch_model.bin:   0%|          | 0.00/1.35G [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/27.0 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/809k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/298 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/400 [00:00<?, ?B/s]

No sentence-transformers model found with name /Users/romainfouilland/.cache/torch/sentence_transformers/dangvantuan_sentence-camembert-large. Creating a new one with MEAN pooling.
OllamaEmbeddings: 100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 44/44 [01:00<00:00,  1.37s/it]


ValueError: Expected each embedding in the embeddings to be a list, got [None, [-1.2770214080810547, 3.922121286392212, -4.678898334503174, 3.826909303665161, 14.898187637329102, -15.866796493530273, 4.0438055992126465, 4.80390739440918, 4.981082916259766, -7.144042015075684, -6.441720008850098, 2.145796298980713, 1.6969751119613647, 3.05902361869812, -2.768139362335205, -8.392414093017578, 2.7403981685638428, -2.2475061416625977, 7.90811824798584, -0.29084330797195435, 7.186946392059326, 2.1424403190612793, 2.3921737670898438, -2.096100330352783, -6.680517673492432, -2.6865456104278564, 1.2299211025238037, -7.608145236968994, 6.790091037750244, 1.5760221481323242, -1.899187684059143, 2.623872756958008, -1.1131871938705444, -1.3422094583511353, 4.222173690795898, -2.553514242172241, -0.303331196308136, 2.2729742527008057, -7.116112232208252, -2.681154251098633, -0.11656540632247925, 1.0928343534469604, -1.4050827026367188, -1.7372225522994995, -1.1810338497161865, 0.40489745140075684, 

In [ ]:
# RETRIEVE
k = 5
query = "Comment faire pour me connecter ?"
# query = "Comment savoir si j'ai des appels en attente ?"
# query = "Comment faire un transfert accompagné ?"
# query = "Quel est mon mot de passe pour me connecter au téléphone ?"

In [ ]:
# - Vectorstore
retriever = vectorstore.as_retriever(search_kwargs={"k": k})
docs = retriever.get_relevant_documents(query)

In [ ]:
# - MultiQuery: make LLM generate similar questions

In [ ]:
# - Contextual Compression: compress retrieved document to extract only the part relevant with the question
# SLOW + IN ENGLISH + could be merged (FILTER + COMPRESSOR)
# Ref.: https://python.langchain.com/docs/modules/data_connection/retrievers/contextual_compression#stringing-compressors-and-document-transformers-together
from langchain.retrievers import ContextualCompressionRetriever
from langchain.retrievers.document_compressors import LLMChainExtractor
compressor = LLMChainExtractor.from_llm(mixtral)
compression_retriever = ContextualCompressionRetriever(
    base_compressor=compressor, base_retriever=retriever
)
compressed_docs = compression_retriever.get_relevant_documents(query)

compressed_docs

In [ ]:
# - Ensemble: use different retrieval algorithms (sparse: BM25 + dense: vector)
# Results are not very good...
from langchain.retrievers import BM25Retriever, EnsembleRetriever
bm25_retriever = BM25Retriever.from_texts(
    list(map(lambda s: s.page_content, all_splits)), metadatas=[{"source": "BM25 sparse similiarity"}] * len(all_splits)
)
bm25_retriever.k = k
# initialize the ensemble retriever
ensemble_retriever = EnsembleRetriever(
    retrievers=[bm25_retriever, retriever], weights=[0.5, 0.5]
)
ensemble_docs = ensemble_retriever.invoke(query)
ensemble_docs

In [ ]:
# - Long-Context Reorder
# Less relevant document will be at the middle of the list and more relevant elements at beginning / end.
from langchain_community.document_transformers import LongContextReorder
reordering = LongContextReorder()
reordered_docs = reordering.transform_documents(ensemble_docs)
# Confirm that the most relevant documents are at beginning and end.
reordered_docs

In [ ]:
# - MultiVector: store multiple vectors for a single element
# ParentDocumentRetriever, Summary vector, Hypothetical Query, ...
# ToDo: investigate Hypothetical Query | Ref.: https://python.langchain.com/docs/modules/data_connection/retrievers/multi_vector#hypothetical-queries

In [ ]:
# - ParentDocumentRetriever: embed small chunks but retrieve with bigger context
from langchain.storage import InMemoryStore
from langchain.retrievers import ParentDocumentRetriever

# This text splitter is used to create the parent documents
parent_splitter = RecursiveCharacterTextSplitter(chunk_size=2000)
# This text splitter is used to create the child documents
# It should create documents smaller than the parent
child_splitter = RecursiveCharacterTextSplitter(chunk_size=400)
# The vectorstore to use to index the child chunks
parent_vectorstore = Chroma(
    collection_name="parent_store", embedding_function=embeddings
)
# The storage layer for the parent documents
parent_store = InMemoryStore()
parent_retriever = ParentDocumentRetriever(
    vectorstore=parent_vectorstore,
    docstore=parent_store,
    child_splitter=child_splitter,
    parent_splitter=parent_splitter,
)
parent_retriever.add_documents(full_data)

In [ ]:
parent_retriever.get_relevant_documents(query)

In [ ]:
# Redo the logic (Ensemble of BM25 + vectorstore => long-context reorder) on parent retriever
# - Ensemble
parent_ensemble_retriever = EnsembleRetriever(
    retrievers=[bm25_retriever, parent_retriever], weights=[0.5, 0.5]
)
parent_ensemble_docs = parent_ensemble_retriever.invoke(query)
parent_ensemble_docs

In [ ]:
# - Reorder
parent_reordered_docs = reordering.transform_documents(parent_ensemble_docs)
# Confirm that the most relevant documents are at beginning and end.
parent_reordered_docs

In [ ]:
# - Self-Query: query itself on metadata
# Too little data here

In [ ]:
# - Time-weighted: decay based on age
# Our vectorstore data has no age

In [ ]:
from langchain.chains import RetrievalQA
# ToDo: How can I add reorder ?
qachain_mixtral = RetrievalQA.from_chain_type(
    llm=mixtral, 
    retriever=parent_ensemble_retriever,
    return_source_documents=True,
    verbose=True
)

In [ ]:
def answer_queries(qachain):
    for query in [
        "Comment faire pour me connecter ?",
        "Comment savoir si j'ai des appels en attente ?",
        "Comment faire un transfert accompagné ?",
        "Quel est mon mot de passe pour me connecter au téléphone ?",
        "Dois-je déconnecter mes T2 ?",
        "Quelle est la météo aujourd'hui ?",
        "Quelle est la hauteur de la tour Eiffel ?"
    ]:
        answer = qachain({"query": query})
        print(f"> {query}:\n{answer}\n\n")

In [ ]:
# Answers back in English!
# answer_queries(qachain_mixtral)

In [ ]:
# ToDo: add more context to query + update system prompt to make it speak French
# Ref.: https://stackoverflow.com/questions/76554411/unable-to-pass-prompt-template-to-retrievalqa-in-langchain
# Ref.: https://community.openai.com/t/how-to-prevent-chatgpt-from-answering-questions-that-are-outside-the-scope-of-the-provided-context-in-the-system-role-message/112027/7
from langchain import PromptTemplate
template = """
Système : Tu es un assistant automatique qui accompagne les utilisateurs du bandeau téléphonique SI-SAMU lors des modes dégradés (aussi appelés modes secours).
N'utilise pas tes connaissances et en t'appuyant UNIQUEMENT sur le Contexte fourni plus bas, réponds à la Question formulée par l'utilisateur en le vouvoyant.
Ne mentionne pas les exemples du Contexte car l'utilisateur n'y a pas accès.
Si tu ne sais pas répondre avec le Contexte uniquement, n'utilise pas tes connaissances et n'invente pas une réponse. Dis à l'utilisateur de contacter le support SI-SAMU.
---
Contexte : {context}
---
Question : {question}
---
Système : Ne donne pas d'information ne venant pas du Contexte.
---
Réponse :
"""
template = """
System: You are helping user of "bandeau téléphonique SI-SAMU" during system failure.
Context information is below. Given the context information and not prior knowledge, answer the query.
Language: Answer in French and using "vous".
---
Context: {context}
---
Question: {question}
---
Réponse :
"""
PROMPT = PromptTemplate(template=template, input_variables=['question', 'context'])
templated_qachain_mixtral = RetrievalQA.from_chain_type(
    llm=mixtral, 
    retriever=parent_ensemble_retriever,
    return_source_documents=True,
    verbose=True,
    chain_type_kwargs={"prompt": PROMPT}
)
templated_qachain_mistral = RetrievalQA.from_chain_type(
    llm=mistral, 
    retriever=parent_ensemble_retriever,
    return_source_documents=True,
    verbose=True,
    chain_type_kwargs={"prompt": PROMPT}
)

In [ ]:
answer_queries(templated_qachain_mixtral)

In [ ]:
answer_queries(templated_qachain_mistral)

In [ ]:
# ToDo: update previous notebook to use a prompt template as well and be able to pass system prompt / examples / context outside of the question !